## Import libraries

In [38]:
import pandas as pd
import numpy as np
import statistics

import plotly
import plotly.graph_objects as go
from plotly.subplots import make_subplots

import sklearn
from sklearn.ensemble import RandomForestClassifier
from sklearn.impute import KNNImputer
from sklearn.preprocessing import OrdinalEncoder

## Data Exploration: import data, check for data size and type

In [39]:
#import train and test data
train = pd.read_csv('train.csv')
test = pd.read_csv('test.csv')

#check the number of rows and columns of data: 1460 rows and 81 columns
print('shape:',train.shape)

# check data variable types: we can observe that there are a lot of columns of 'object' data type
display(train.info())
display(test.info())

# column 'Id' is simply the row numbers, drop it.
train.drop(columns = ['Id'], inplace = True)
test.drop(columns = ['Id'], inplace = True)

shape: (1460, 81)
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1460 entries, 0 to 1459
Data columns (total 81 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   Id             1460 non-null   int64  
 1   MSSubClass     1460 non-null   int64  
 2   MSZoning       1460 non-null   object 
 3   LotFrontage    1201 non-null   float64
 4   LotArea        1460 non-null   int64  
 5   Street         1460 non-null   object 
 6   Alley          91 non-null     object 
 7   LotShape       1460 non-null   object 
 8   LandContour    1460 non-null   object 
 9   Utilities      1460 non-null   object 
 10  LotConfig      1460 non-null   object 
 11  LandSlope      1460 non-null   object 
 12  Neighborhood   1460 non-null   object 
 13  Condition1     1460 non-null   object 
 14  Condition2     1460 non-null   object 
 15  BldgType       1460 non-null   object 
 16  HouseStyle     1460 non-null   object 
 17  OverallQual    1460 non-null   int

None

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1459 entries, 0 to 1458
Data columns (total 80 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   Id             1459 non-null   int64  
 1   MSSubClass     1459 non-null   int64  
 2   MSZoning       1455 non-null   object 
 3   LotFrontage    1232 non-null   float64
 4   LotArea        1459 non-null   int64  
 5   Street         1459 non-null   object 
 6   Alley          107 non-null    object 
 7   LotShape       1459 non-null   object 
 8   LandContour    1459 non-null   object 
 9   Utilities      1457 non-null   object 
 10  LotConfig      1459 non-null   object 
 11  LandSlope      1459 non-null   object 
 12  Neighborhood   1459 non-null   object 
 13  Condition1     1459 non-null   object 
 14  Condition2     1459 non-null   object 
 15  BldgType       1459 non-null   object 
 16  HouseStyle     1459 non-null   object 
 17  OverallQual    1459 non-null   int64  
 18  OverallC

None

## Data Exploration: check for distribution of target 'SalePrice'
The target is a continuous variable
- From the boxplot, we can make the following observations:
       - The target has a wide range of 755,000 - 34,900 = 720,100
       - Majority of the data falls between the range 129,975-214,000
       - The distribution is skwed to the right.
       

In [40]:
display(train['SalePrice'].describe())

fig = go.Figure()
fig.add_trace(go.Box(y=train['SalePrice'], name = 'SalePrice', boxpoints='all', ))
fig.show()

count      1460.000000
mean     180921.195890
std       79442.502883
min       34900.000000
25%      129975.000000
50%      163000.000000
75%      214000.000000
max      755000.000000
Name: SalePrice, dtype: float64

In [ ]:
#remove the outliers
train = train.loc[train.loc[:,'SalePrice'] < 745000]

## Data Exploration & Preprocessing: check for null values

In [41]:
#Check for proportion of null data under each column.
#Observations: Both train and test datasets are same in terms of top 5 variables with highest % of null values.

def check_null(data):
    count = data.isnull().sum().sort_values(ascending=False)
    pctg = data.isnull().sum().sort_values(ascending=False)/len(data)*100
    missing_data = pd.concat([count, pctg], axis=1, keys=['Count', 'Percent'])
    display(missing_data.head(20))
    return missing_data[missing_data['Count']>0]
    
train_miss = check_null(train)
test_miss = check_null(test)

Count    Percent
PoolQC         1453  99.520548
MiscFeature    1406  96.301370
Alley          1369  93.767123
Fence          1179  80.753425
FireplaceQu     690  47.260274
LotFrontage     259  17.739726
GarageYrBlt      81   5.547945
GarageCond       81   5.547945
GarageType       81   5.547945
GarageFinish     81   5.547945
GarageQual       81   5.547945
BsmtExposure     38   2.602740
BsmtFinType2     38   2.602740
BsmtCond         37   2.534247
BsmtQual         37   2.534247
BsmtFinType1     37   2.534247
MasVnrArea        8   0.547945
MasVnrType        8   0.547945
Electrical        1   0.068493
MSSubClass        0   0.000000

Count    Percent
PoolQC         1456  99.794380
MiscFeature    1408  96.504455
Alley          1352  92.666210
Fence          1169  80.123372
FireplaceQu     730  50.034270
LotFrontage     227  15.558602
GarageYrBlt      78   5.346127
GarageFinish     78   5.346127
GarageQual       78   5.346127
GarageCond       78   5.346127
GarageType       76   5.209047
BsmtCond         45   3.084304
BsmtExposure     44   3.015764
BsmtQual         44   3.015764
BsmtFinType2     42   2.878684
BsmtFinType1     42   2.878684
MasVnrType       16   1.096642
MasVnrArea       15   1.028101
MSZoning          4   0.274160
Functional        2   0.137080

The first attempt is to directly drop columns with over 90% null values, that is, the first three variables: 'PoolQC', 'MiscFeature','Alley'.

However, upon reading the data_description.txt file, I noticed that null values for some categorical variables
mean non-existent of the feature. Therefore, the null values for theses variables should be treated as another
category.
Below summarized those categorical variables(unless stated nominal, the variables are ordinal):

- Alley:NA->No alley access(nomial)
- BsmtQual:NA->No Basement
- BsmtCond: NA->No Basement
- BsmtExposure: NA->No Basement
- BsmtFinType1: NA->No Basement
- BsmtFinType2:NA->No Basement
- FireplaceQu: NA->No Fireplace
- GarageType: NA->No Garage(nominal)
- GarageFinish:NA->No Garage
- GarageQual: NA->No Garage
- GarageCond: NA->No Garage
- PoolQC:NA->No Pool
- Fence: NA->No Fence
- MiscFeature:NA->None(nominal)

Therefore, will encode the null values of these variables into string '0'.

In [42]:
#check for null values
fill_null_var = ["Alley","BsmtQual","BsmtCond","BsmtExposure","BsmtFinType1","BsmtFinType2","FireplaceQu","GarageType",
                "GarageFinish","GarageQual","GarageCond","PoolQC","Fence","MiscFeature"]

display(train[fill_null_var].isnull().sum().sort_values(ascending=False))
display(test[fill_null_var].isnull().sum().sort_values(ascending=False))

#check for categories present in each of these variables
#there are no category '0', thus will use '0' to fill in the null values
check_df = pd.concat([train[fill_null_var], test[fill_null_var]],axis = 0)
for c in check_df.columns:
    display(check_df[c].value_counts(dropna = False))

PoolQC          1453
MiscFeature     1406
Alley           1369
Fence           1179
FireplaceQu      690
GarageType        81
GarageFinish      81
GarageQual        81
GarageCond        81
BsmtExposure      38
BsmtFinType2      38
BsmtQual          37
BsmtCond          37
BsmtFinType1      37
dtype: int64

PoolQC          1456
MiscFeature     1408
Alley           1352
Fence           1169
FireplaceQu      730
GarageFinish      78
GarageQual        78
GarageCond        78
GarageType        76
BsmtCond          45
BsmtQual          44
BsmtExposure      44
BsmtFinType1      42
BsmtFinType2      42
dtype: int64

NaN     2721
Grvl     120
Pave      78
Name: Alley, dtype: int64

TA     1283
Gd     1209
Ex      258
Fa       88
NaN      81
Name: BsmtQual, dtype: int64

TA     2606
Gd      122
Fa      104
NaN      82
Po        5
Name: BsmtCond, dtype: int64

...

TA     2604
NaN     159
Fa      124
Gd       24
Po        5
Ex        3
Name: GarageQual, dtype: int64

TA     2654
NaN     159
Fa       74
Gd       15
Po       14
Ex        3
Name: GarageCond, dtype: int64

NaN    2909
Gd        4
Ex        4
Fa        2
Name: PoolQC, dtype: int64

NaN      2348
MnPrv     329
GdPrv     118
GdWo      112
MnWw       12
Name: Fence, dtype: int64

NaN     2814
Shed      95
Gar2       5
Othr       4
TenC       1
Name: MiscFeature, dtype: int64

In [44]:
#encode the null values of variables into string '0'.
train[fill_null_var] = train[fill_null_var].fillna(value='0')
test[fill_null_var] = test[fill_null_var].fillna(value='0')

#check again for null values
display(train[fill_null_var].isnull().sum().sort_values(ascending=False))
display(test[fill_null_var].isnull().sum().sort_values(ascending=False))

Alley           0
BsmtQual        0
BsmtCond        0
BsmtExposure    0
BsmtFinType1    0
BsmtFinType2    0
FireplaceQu     0
GarageType      0
GarageFinish    0
GarageQual      0
GarageCond      0
PoolQC          0
Fence           0
MiscFeature     0
dtype: int64

Alley           0
BsmtQual        0
BsmtCond        0
BsmtExposure    0
BsmtFinType1    0
BsmtFinType2    0
FireplaceQu     0
GarageType      0
GarageFinish    0
GarageQual      0
GarageCond      0
PoolQC          0
Fence           0
MiscFeature     0
dtype: int64

## Explore continuous data 

From the scatterplot, it can be observed that some variables with type not equal to 'object' seems 
to be categorical. 
<br>After checking with the data description given on the meaning of the variable, 
more variables are considered to be categorical: 
<br> ['MSSubClass', 'OverallQual', 'OverallCond','BsmtFullBath','BsmtHalfBath','FullBath','HalfBath','BedroomAbvGrd',
'KitchenAbvGr' , 'TotRmsAbvGr', 'Fireplaces', 'GarageCars', 'MoSold','YrSold','YearBuilt','YearRemodAdd']

In [45]:
#get all the categorical variables
categorical_vars = []
for i in train.columns:
    if(train[i].dtypes == 'object'):
        categorical_vars.append(i)

#get all the variables that are not of type 'object'
continuous_vars = []
for i in train.columns:
    if(train[i].dtypes != 'object' and i != 'SalePrice'):
        continuous_vars.append(i)

In [46]:
#plot scatter plot for each continuous variables
fig = make_subplots(rows=10, cols=4, shared_yaxes=False,row_heights = 10*[0.6],
subplot_titles = (continuous_vars))
                    
r = 1
c = 1
for col in continuous_vars:

            fig.add_trace(go.Scatter(x=train[col], y = train['SalePrice'],name =col, mode = 'markers'
                          ) ,row=r, col=c)

            if(c%4 == 0): 
                r+=1 
                c = 1
            else:
                c+=1

fig.update_layout(title="Continuous Variables Exploration",height = 1500)
fig.show()


    

## Explore categorical variables using box plots and histograms

In [47]:
#Add the variables selected from previous section 
categorical_vars += ['MSSubClass', 'OverallQual', 'OverallCond','BsmtFullBath','BsmtHalfBath','FullBath',
                        'HalfBath','BedroomAbvGr','KitchenAbvGr' , 'TotRmsAbvGrd', 'Fireplaces', 'GarageCars',
                    'MoSold','YrSold','YearBuilt','YearRemodAdd','GarageYrBlt']

#plot boxplots for each categorical variables
fig = make_subplots(rows=16, cols=4, shared_yaxes=False,row_heights = 16*[0.9],
subplot_titles = (categorical_vars))
                    
r = 1
c = 1
for col in categorical_vars:

            fig.add_trace(go.Box(x=train[col], y = train['SalePrice'],name =col, text = col
                          ) ,row=r, col=c)

            if(c%4 == 0): 
                r+=1 
                c = 1
            else:
                c+=1

fig.update_layout(title="Categorical Variables Exploration",height = 2000)
fig.show()

In [48]:
#combine train and test data
print(train.shape, test.shape)
concated_df = pd.concat([train, test],axis = 0)
concated_df.reset_index(drop = True, inplace = True)
print(concated_df.shape)

(1460, 80) (1459, 79)
(2919, 80)


From the boxplots, it can be observed that varibales can have very little number of counts for some categories.
<br>Below plots the histogram of theses variables.
<br>We can observe that the distribution can be very imbalanced for some variables with some categories having count < 10.

In [49]:
#check the selected categorical variables
to_check = ['Utilities','Condition1','Condition2','RoofMatl','Exterior1st',
           'Exterior2nd','ExterCond','BsmtCond','Heating','HeatingQC',
           'Electrical','Functional','GarageCond','BsmtFullBath','KitchenAbvGr']
        
#plot boxplots for each categorical variables to check
fig = make_subplots(rows=5, cols=4, shared_yaxes=False,row_heights = 5*[0.5],
subplot_titles = (to_check))
                    
r = 1
c = 1
for col in to_check:
            plot_data = pd.DataFrame(concated_df[col].value_counts(dropna=False,ascending = True)).reset_index()
            plot_data['index'] = plot_data['index'].astype(str)
            plot_data['pctg'] = plot_data[col] #round(plot_data[col]/sum(plot_data[col])*100,2)
            fig.add_trace(go.Bar(x=plot_data['index'], y = plot_data[col],name =col, 
                          text=[f'{i}' for i in plot_data['pctg']]) ,row=r, col=c)
            if(c%4 == 0): 
                r+=1 
                c = 1
            else:
                c+=1


fig.update_layout(title="Categorical Variables Exploration",height = 800)
fig.show()

## Fill in missing values for continuous variables using KNN imputation

In [50]:
#update list storing the continuous variables
conti_vars_updated = []
for i in continuous_vars:
    if i in categorical_vars:
        continue
    else:
        conti_vars_updated.append(i)
        
conti_vars_updated

['LotFrontage',
 'LotArea',
 'MasVnrArea',
 'BsmtFinSF1',
 'BsmtFinSF2',
 'BsmtUnfSF',
 'TotalBsmtSF',
 '1stFlrSF',
 '2ndFlrSF',
 'LowQualFinSF',
 'GrLivArea',
 'GarageArea',
 'WoodDeckSF',
 'OpenPorchSF',
 'EnclosedPorch',
 '3SsnPorch',
 'ScreenPorch',
 'PoolArea',
 'MiscVal']

In [51]:
continuous_df = concated_df[conti_vars_updated].copy()

#impute the missing values
knn = KNNImputer(n_neighbors = 5)
knn.fit(continuous_df)
df_opt = knn.transform(continuous_df)

#combine the filled columns with the target column
df_opt = pd.DataFrame(df_opt)
df_opt.columns = continuous_df.columns

#check for null values after imputation
display(df_opt.isnull().sum().sort_values(ascending=False))

#add the target column
df_opt.loc[:,'SalePrice'] = concated_df.loc[:,'SalePrice']
df_opt_continuous = df_opt

LotFrontage      0
GrLivArea        0
PoolArea         0
ScreenPorch      0
3SsnPorch        0
EnclosedPorch    0
OpenPorchSF      0
WoodDeckSF       0
GarageArea       0
LowQualFinSF     0
LotArea          0
2ndFlrSF         0
1stFlrSF         0
TotalBsmtSF      0
BsmtUnfSF        0
BsmtFinSF2       0
BsmtFinSF1       0
MasVnrArea       0
MiscVal          0
dtype: int64

## Imputate missing values for categorial variables and encode categorical variables

In [57]:
#group categorical variables into nominal and ordinal variables 

#nominal variables
nominal_var = ["MSSubClass","MSZoning","Street","Alley","LotShape","LandContour","Utilities","LotConfig",
              "LandSlope","Neighborhood","Condition1","Condition2","BldgType","HouseStyle","RoofStyle",
              "RoofMatl","Exterior1st","Exterior2nd","MasVnrType","Foundation","Heating","CentralAir",
              "Electrical","GarageType","SaleType","SaleCondition","MiscFeature","Fence"]

#encode nominal variables
categorical_nominal_df =  concated_df[nominal_var].copy()

encoder = OrdinalEncoder()
categorical_nominal_df = encoder.fit_transform(categorical_nominal_df)
categorical_nominal_df = pd.DataFrame(categorical_nominal_df)
categorical_nominal_df.columns = nominal_var

In [58]:
#ordinal variables
ordinal_var = []
for i in categorical_vars:
    if(i not in nominal_var):
        ordinal_var.append(i)

In [59]:
#create the mapping of categories to integer
mapping = {
       "Ex": 5,"Gd": 4,"TA": 3,"Fa": 2, "Po": 1,'0': 0,
                       'Av': 3, 'Mn': 2, 'No': 1,
       "GLQ": 6,  "ALQ": 5,  "BLQ": 4,  "Rec": 3,  "LwQ": 2,  "Unf": 1,
       "Typ": 8, "Min1": 7, "Min2": 6,  "Mod": 5,  "Maj1": 4, "Maj2": 3, "Sev": 2, "Sal":1,
       "Fin": 3, "RFn": 2, 'Unf': 1,
       'Y': 3, 'P': 2, 'N': 1,
}

#encode the ordinal variables
concated_df[ordinal_var] = concated_df[ordinal_var].replace(mapping)

In [68]:
#combine the encoded results for both nominal and ordinal variables
concated_df[nominal_var] = categorical_nominal_df[nominal_var]

#combine the results for both categorical and continuous variables
concated_df[conti_vars_updated] = df_opt_continuous[conti_vars_updated]

In [70]:
#impute the missing values
knn = KNNImputer(n_neighbors = 5)
knn.fit(concated_df)
df_opt = knn.transform(concated_df)

# round the imputated values to integer
df_opt = pd.DataFrame(df_opt)
df_opt.columns = concated_df.columns
for i in df_opt[categorical_vars]:
    df_opt[i] = round(df_opt[i],0)

#check for null values after imputation
display(df_opt.isnull().sum().sort_values(ascending=False))


MSSubClass     0
MSZoning       0
GarageYrBlt    0
GarageType     0
FireplaceQu    0
              ..
MasVnrArea     0
MasVnrType     0
Exterior2nd    0
Exterior1st    0
SalePrice      0
Length: 80, dtype: int64

In [71]:
#apply one-hot encoding to nominal variables
df_concated_final = pd.get_dummies(df_opt, columns=nominal_var, drop_first=True)
print(df_concated_final.shape)

(2919, 223)


## Output the preprocessed train and test data

In [77]:
#split the data into train and test datasets and output to csv file
train_preprocessed = df_concated_final.loc[:1459]
test_preprocessed = df_concated_final.loc[1460:]
test_preprocessed.drop(columns = ['SalePrice'], inplace = True)

train_preprocessed.to_csv('train_preprocessed_2.csv', index = False)
test_preprocessed.to_csv('test_preprocessed_2.csv', index = False)

C:\Users\qiyun\miniconda3\lib\site-packages\pandas\core\frame.py:4315: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

